In [69]:
import pandas as pd
import numpy as np
import plotly.offline as pyo
import plotly.graph_objs as go

+# Explonatery Data Analysis

In [70]:
from google.colab import files
uploaded = files.upload()

Saving price_changes.csv to price_changes (1).csv
Saving sales_small.csv to sales_small (1).csv
Saving products.csv to products (1).csv


In [71]:
import io  
df_sales = pd.read_csv(io.BytesIO(uploaded['sales_small.csv']))
df_sales.head()

sales_small.ProductID  ... sales_small.StoresWithSalesCount
0              135fc45e  ...                           0.0078
1              1ff41410  ...                           0.0389
2              22125db2  ...                           0.0039
3              25e07883  ...                           0.0194
4              2729a59e  ...                           0.0350

[5 rows x 13 columns]

In [72]:
df_prices_change = pd.read_csv(io.BytesIO(uploaded['price_changes.csv']))
df_prices_change.head()

price_changes.ProductID  ...  price_changes.CSP
0                100ba933  ...             14.033
1                100ba933  ...             12.683
2                101cfc62  ...             16.733
3                1021879c  ...             13.583
4                10328ad7  ...             13.133

[5 rows x 7 columns]

In [73]:
df_products = pd.read_csv(io.BytesIO(uploaded['products.csv']))
df_products.head()

products.ProductID products.Season  ... products.Class products.SubClass
0           110e1664               L  ...       57dedfae          e5db0621
1           11430072               L  ...       bb900370          fed6cf53
2           11660a96               L  ...       8f5e4e2f          52fc415a
3           116e2878               L  ...       96d57a3c          62defb1f
4           1.19E+81               L  ...       8f5e4e2f          52fc415a

[5 rows x 6 columns]

In [74]:
df_sales.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 44167 entries, 0 to 44166
Data columns (total 13 columns):
 #   Column                              Non-Null Count  Dtype  
---  ------                              --------------  -----  
 0   sales_small.ProductID               44167 non-null  object 
 1   sales_small.Channel                 44167 non-null  object 
 2   sales_small.Country                 44167 non-null  object 
 3   sales_small.WeekKey                 44167 non-null  int64  
 4   sales_small.CSP                     44167 non-null  float64
 5   sales_small.SalesVolume             44167 non-null  int64  
 6   sales_small.TotalStockVolume        44167 non-null  int64  
 7   sales_small.StoreStockVolume        44167 non-null  int64  
 8   sales_small.DepotStockVolume        44167 non-null  int64  
 9   sales_small.FutureCommitmentVolume  44167 non-null  int64  
 10  sales_small.IntakeVolume            44167 non-null  int64  
 11  sales_small.StoresWithStockCount    44167

In [75]:

df_sales['date'] = pd.to_datetime((df_sales['sales_small.WeekKey']-1).astype(str) + "6", format="%Y%U%w")
#df_sales=df_sales.astype({'sales_small.WeekKey':str})
df_sales['Month'] = df_sales['date'].dt.month_name()
df_sales['Year-Month']=df_sales['Month'] + '-' + (pd.DatetimeIndex(df_sales['date']).year).astype(str)
df_sales['Year-Month']
sales_2015=df_sales[df_sales['Year-Month'].str.contains('2015')]
sales_2016=df_sales[df_sales['Year-Month'].str.contains('2016')]
df_weekly_sales15=sales_2015.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
df_weekly_sales16=sales_2016.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
df_weekly_sales15.head()

Year-Month
January-2015     12.481763
February-2015    18.839869
March-2015       17.268442
April-2015       17.350158
May-2015         17.334724
Name: sales_small.SalesVolume, dtype: float64

In [76]:
df_monthly=df_sales.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume','sales_small.StoresWithStockCount','sales_small.StoresWithSalesCount'].mean()
df_monthly=df_monthly.reset_index()
df_monthly

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



Year-Month  ...  sales_small.StoresWithSalesCount
0     January-2015  ...                          0.055286
1    February-2015  ...                          0.079537
2       March-2015  ...                          0.081754
3       April-2015  ...                          0.080146
4         May-2015  ...                          0.072400
5        June-2015  ...                          0.046230
6        July-2015  ...                          0.019533
7      August-2015  ...                          0.009699
8   September-2015  ...                          0.004185
9     October-2015  ...                          0.024767
10   November-2015  ...                          0.033913
11   December-2015  ...                          0.041770
12    January-2016  ...                          0.046990
13   February-2016  ...                          0.052072

[14 rows x 4 columns]

In [77]:
fig=go.Figure()
fig.add_trace(go.Scatter(x=df_monthly['Year-Month'],y=df_monthly['sales_small.SalesVolume'],mode='lines+markers',marker_color='navy', name='Avg Sales / Month') )
fig.update_layout(go.Layout(xaxis_title='Month',yaxis_title='Average Sales Per Month'))
#fig = go.Figure(data=data, layout=layout)
#fig.add_trace(go.Scatter(x=df_monthly['Year-Month'], y=df_monthly['sales_small.StoresWithStockCount'], mode='lines+markers', name='Avg % of stock count / Month',marker_color='#0097A9'))
#fig.add_trace(go.Scatter(x=df_monthly['Year-Month'], y=df_monthly['sales_small.StoresWithSalesCount'], mode='lines+markers', name='Avg % of sales count / Month',marker_color='lightsalmon'))
pyo.iplot(fig);

In [78]:
df_monthly_channel=df_sales.groupby(['Year-Month','sales_small.Channel'],sort=False)['sales_small.SalesVolume'].mean()
df_monthly_channel=df_monthly_channel.reset_index()
df_monthly_stores=df_monthly_channel[df_monthly_channel['sales_small.Channel']=='Stores']
df_monthly_online=df_monthly_channel[df_monthly_channel['sales_small.Channel']=='Online']
df_monthly_online

Year-Month sales_small.Channel  sales_small.SalesVolume
1     January-2015              Online                 2.837607
3    February-2015              Online                 3.405039
4       March-2015              Online                 4.181818
6       April-2015              Online                 3.456212
8         May-2015              Online                 3.706951
10       June-2015              Online                 2.200758
12       July-2015              Online                 1.467601
14     August-2015              Online                 1.277108
17  September-2015              Online                 1.165017
19    October-2015              Online                 2.256272
21   November-2015              Online                 2.627419
23   December-2015              Online                 2.648376
25    January-2016              Online                 2.456643
27   February-2016              Online                 3.336053

In [79]:
fig=go.Figure()
#fig.add_trace(go.Scatter(x=df_monthly['Year-Month'],y=df_monthly['sales_small.SalesVolume'],mode='lines+markers',marker_color='navy', name='Avg Sales / Month') )
fig.update_layout(go.Layout(xaxis_title='Month',yaxis_title='Average Sales Per Month'))
#fig = go.Figure(data=data, layout=layout)
fig.add_trace(go.Scatter(x=df_monthly_stores['Year-Month'], y=df_monthly_stores['sales_small.SalesVolume'], mode='lines+markers', name='Stores Avg Sales / Month',marker_color='#0097A9'))
fig.add_trace(go.Scatter(x=df_monthly_online['Year-Month'], y=df_monthly_online['sales_small.SalesVolume'], mode='lines+markers', name='Online Avg Sales / Month',marker_color='lightsalmon'))
pyo.iplot(fig);

In [80]:
trace = go.Bar(x=list(df_weekly_sales15.index), y=list(df_weekly_sales15.values), marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='2015 average sales for every Month',xaxis=dict(type='category',tickangle=45),xaxis_title='Month',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
fig.update_layout(yaxis=dict(range=[0, 20]))
pyo.iplot(fig);

In [81]:
df_weekly_sales=df_sales.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
trace = go.Bar(x=list(df_weekly_sales.index), y=list(df_weekly_sales.values), marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='Average sales for every Month',xaxis=dict(type='category',tickangle=45),xaxis_title='Month',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
fig.update_layout(yaxis=dict(range=[0, 20]))
pyo.iplot(fig);

In [82]:
df_sales['Year']=pd.DatetimeIndex(df_sales['date']).year
df_sales['Year']=df_sales['Year'].astype(str)
df_sales.head()

sales_small.ProductID sales_small.Channel  ...    Year-Month  Year
0              135fc45e              Stores  ...  January-2015  2015
1              1ff41410              Stores  ...  January-2015  2015
2              22125db2              Stores  ...  January-2015  2015
3              25e07883              Stores  ...  January-2015  2015
4              2729a59e              Stores  ...  January-2015  2015

[5 rows x 17 columns]

In [83]:
avgs_groupby_year=df_sales.groupby(['Year'],sort=False)['sales_small.CSP','sales_small.SalesVolume','sales_small.TotalStockVolume',
                                                        'sales_small.StoreStockVolume','sales_small.DepotStockVolume','sales_small.FutureCommitmentVolume',
                                                        'sales_small.IntakeVolume','sales_small.StoresWithStockCount','sales_small.StoresWithSalesCount'].mean()
avgs_groupby_year

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



sales_small.CSP  ...  sales_small.StoresWithSalesCount
Year                   ...                                  
2015        13.433299  ...                          0.044037
2016        13.903257  ...                          0.049441

[2 rows x 9 columns]

In [84]:

xaxiis=avgs_groupby_year.index
fig = go.Figure(data=[
    go.Bar(name='Average Selling Price', x=xaxiis, y=avgs_groupby_year['sales_small.CSP'] ,marker_color='indianred'),
    go.Bar(name='Average Sales Volume', x=xaxiis, y=avgs_groupby_year['sales_small.SalesVolume']  ,marker_color='skyblue'),
    go.Bar(name='Average Total Stock Volume', x=xaxiis, y=avgs_groupby_year['sales_small.TotalStockVolume']  ,marker_color='navy'),
    go.Bar(name='Average Store Stock Volume', x=xaxiis, y=avgs_groupby_year['sales_small.StoreStockVolume']  ,marker_color='green'),
    go.Bar(name='Average Depot Stock Volume', x=xaxiis, y=avgs_groupby_year['sales_small.DepotStockVolume']  ,marker_color='#C4D600'),
    go.Bar(name='Average Future Commit. Volume', x=xaxiis, y=avgs_groupby_year['sales_small.FutureCommitmentVolume']  ,marker_color='grey'),
    go.Bar(name='Average Intake Volume', x=xaxiis, y=avgs_groupby_year['sales_small.IntakeVolume']  ,marker_color='orange'),
    go.Bar(name='Average Stores with stock count', x=xaxiis, y=avgs_groupby_year['sales_small.StoresWithStockCount']  ,marker_color='#43B02A'),
    go.Bar(name='Average Stores with sales count', x=xaxiis, y=avgs_groupby_year['sales_small.StoresWithSalesCount']  ,marker_color='#0097A9')
])
# Change the bar mode
fig.update_layout(barmode='stack',xaxis=dict(type='category'))
fig.show()

In [85]:
sales_2016['sales_small.SalesVolume'].sum()

121062

In [86]:
avgs_groupby_year.index.dtype

dtype('O')

In [87]:

index=['January-2016','February-2016','March-2016','April-2016','May-2016','June-2016','July-2016','August-2016','September-2016',
                         'October-2016','November-2016','December-2016']
data=[10.009856,10.963421,0,0,0,0,0,0,0,0,0,0]
df_weekly_sales16=pd.Series(data=data,index=index)
df_weekly_sales16

January-2016      10.009856
February-2016     10.963421
March-2016         0.000000
April-2016         0.000000
May-2016           0.000000
June-2016          0.000000
July-2016          0.000000
August-2016        0.000000
September-2016     0.000000
October-2016       0.000000
November-2016      0.000000
December-2016      0.000000
dtype: float64

In [88]:
trace = go.Bar(x=list(df_weekly_sales16.index), y=list(df_weekly_sales16.values), marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='2016 average sales for every Month',xaxis=dict(type='category'),xaxis_title='Month',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);

In [89]:
channel_count_2015=sales_2015['sales_small.Channel'].value_counts()
channel_count_2015 =channel_count_2015.reset_index()
fig = go.Figure(data=go.Pie(labels=channel_count_2015['index'],values=channel_count_2015['sales_small.Channel']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=20,
                  marker=dict(colors=['skyblue','navy'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of sales from store vs online in 2015')
fig.show()

In [90]:
country_count_2015=sales_2015['sales_small.Country'].value_counts()
country_count_2015 =country_count_2015.reset_index()
fig = go.Figure(data=go.Pie(labels=country_count_2015['index'],values=country_count_2015['sales_small.Country']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=20,
                  marker=dict(colors=['skyblue','navy'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of sales from Country A vs Country B in 2015')
fig.show()

In [91]:
channel_count_2016=sales_2016['sales_small.Channel'].value_counts()
channel_count_2016 =channel_count_2016.reset_index()
fig = go.Figure(data=go.Pie(labels=channel_count_2016['index'],values=channel_count_2016['sales_small.Channel']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=20,
                  marker=dict(colors=['skyblue','navy'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of sales from store vs online in 2016')
fig.show()

In [92]:
channel_count_2016=sales_2016['sales_small.Country'].value_counts()
channel_count_2016 =channel_count_2016.reset_index()
fig = go.Figure(data=go.Pie(labels=channel_count_2016['index'],values=channel_count_2016['sales_small.Country']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=20,
                  marker=dict(colors=['skyblue','navy'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of sales from Country A vs Country B in 2016')
fig.show()

In [93]:
top20_2015=sales_2015.groupby(['sales_small.ProductID'])['sales_small.SalesVolume'].mean()
top20_2015=top20_2015.reset_index()
top20_2015=top20_2015.nlargest(20,['sales_small.SalesVolume'],keep='all')
top20_2015.head()

sales_small.ProductID  sales_small.SalesVolume
643              f5c65eec               110.958333
641              f57697c2                93.333333
294               7d4e30b                83.500000
496              bfdbbeef                80.913043
303              80439b0f                78.550000

In [94]:
trace = go.Bar(x=top20_2015['sales_small.ProductID'], y=top20_2015['sales_small.SalesVolume'], marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='Top 20 Products with Average Sales Volume in 2015',xaxis=dict(type='category'),xaxis_title='Product ID',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);

In [95]:
top20_2016=sales_2016.groupby(['sales_small.ProductID'])['sales_small.SalesVolume'].mean()
top20_2016=top20_2016.reset_index()
top20_2016=top20_2016.nlargest(20,['sales_small.SalesVolume'],keep='all')
top20_2016.head()

sales_small.ProductID  sales_small.SalesVolume
220              4e7ac29d               145.111111
463              8f4891f7               120.500000
111              3130d4a9               109.666667
557              a79c5c41                92.187500
118              342e6e50                87.214286

In [96]:
trace = go.Bar(x=top20_2016['sales_small.ProductID'], y=top20_2016['sales_small.SalesVolume'], marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='Top 20 Products with Average Sales Volume in 2016',xaxis=dict(type='category'),xaxis_title='Product ID',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);

In [97]:
df_sales_remove_outliers=df_sales[df_sales['sales_small.TotalStockVolume']<2000]
data=go.Scatter(x=df_sales_remove_outliers['sales_small.TotalStockVolume'],y=df_sales_remove_outliers['sales_small.SalesVolume'],mode='markers',marker_color='blue')
layout=go.Layout(title='Relation between Total stock volume and Price volume' ,xaxis_title='Total Stock Volume',yaxis_title='Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);


In [98]:
df_sales.rename(columns = {'sales_small.ProductID':'ProductID'}, inplace = True)
df_prices_change.rename(columns = {'price_changes.ProductID':'ProductID'}, inplace = True)
df_sales.rename(columns = {'sales_small.WeekKey':'WeekKey'}, inplace = True)
df_prices_change.rename(columns = {'price_changes.WeekKey':'WeekKey'}, inplace = True)
df_sales.rename(columns = {'sales_small.Channel':'Channel'}, inplace = True)
df_prices_change.rename(columns = {'price_changes.Channel':'Channel'}, inplace = True)
df_sales.rename(columns = {'sales_small.Country':'Country'}, inplace = True)
df_prices_change.rename(columns = {'price_changes.Country':'Country'}, inplace = True)

merged_df=pd.merge(df_sales, df_prices_change, on=["ProductID"])
merged_df.head(8)

ProductID Channel_x  ... price_changes.previous_CSP  price_changes.CSP
0  135fc45e    Stores  ...                     18.984             16.283
1  135fc45e    Stores  ...                     16.283             14.483
2  135fc45e    Stores  ...                     14.483             13.133
3  135fc45e    Stores  ...                     13.133             10.882
4  135fc45e    Stores  ...                     18.984             16.283
5  135fc45e    Stores  ...                     16.283             14.483
6  135fc45e    Stores  ...                     14.483             13.133
7  135fc45e    Stores  ...                     13.133             10.882

[8 rows x 23 columns]

In [99]:
#
prices_cat=[]
for index, row in merged_df.iterrows():
  if str(row['sales_small.CSP'])==str(row['price_changes.OSP']):
      prices_cat.append('OSP')
  elif str(row['sales_small.CSP'])==str(row['price_changes.previous_CSP']):
      prices_cat.append('Previous CSP')
  elif str(row['sales_small.CSP'])==str(row['price_changes.CSP']):
      prices_cat.append('CSP')
  else:
      prices_cat.append('Other')
merged_df['Prices-Category']=prices_cat
merged_df.head(-20)


ProductID Channel_x  ... price_changes.CSP  Prices-Category
0       135fc45e    Stores  ...            16.283              OSP
1       135fc45e    Stores  ...            14.483              OSP
2       135fc45e    Stores  ...            13.133              OSP
3       135fc45e    Stores  ...            10.882              OSP
4       135fc45e    Stores  ...            16.283              OSP
...          ...       ...  ...               ...              ...
244640  d9bd3ebf    Stores  ...            11.782              CSP
244641  d9bd3ebf    Stores  ...            12.232            Other
244642  d9bd3ebf    Stores  ...            11.782              CSP
244643  e0a2110d    Online  ...            13.583              OSP
244644  e0a2110d    Online  ...            13.583              OSP

[244645 rows x 24 columns]

In [100]:
prices_cat_avg_sales=merged_df.groupby(['Prices-Category'],sort=False)['sales_small.SalesVolume'].mean()
prices_cat_avg_sales2=prices_cat_avg_sales[0:3]
prices_cat_avg_sales2=prices_cat_avg_sales2.reset_index()
prices_cat_avg_sales2

Prices-Category  sales_small.SalesVolume
0             OSP                17.599739
1             CSP                 6.565391
2    Previous CSP                 8.955689

In [101]:
trace = go.Bar(x=prices_cat_avg_sales2['Prices-Category'], y=prices_cat_avg_sales2['sales_small.SalesVolume'], marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='average sales for every price category',xaxis=dict(type='category',categoryorder='total descending'),xaxis_title='Price Category',yaxis_title='Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);

In [102]:
merged_df['Year']=pd.DatetimeIndex(merged_df['date']).year
groupby_year_df=merged_df.groupby(['Prices-Category','Year'],sort=False)['sales_small.SalesVolume'].mean()
groupby_year_df=groupby_year_df.reset_index()
groupby_year_df=groupby_year_df.drop([3,4])
groupby_year_df

Prices-Category  Year  sales_small.SalesVolume
0             OSP  2015                17.893466
1             CSP  2015                 6.870448
2    Previous CSP  2015                 9.266678
5             CSP  2016                 5.312053
6    Previous CSP  2016                 6.219365
7             OSP  2016                13.208827

In [103]:
import plotly.express as px
fig = go.Figure(data=[
    go.Bar(name='2015', x=groupby_year_df['Prices-Category'][0:3], y=groupby_year_df['sales_small.SalesVolume'][0:3],marker_color='skyblue'),
    go.Bar(name='2016', x=groupby_year_df['Prices-Category'][3:], y=groupby_year_df['sales_small.SalesVolume'][3:],marker_color='navy')

])
# Change the bar mode
fig.update_layout(barmode='group',title='Price category vs avg sales in both years',
                  xaxis_title='Price Category',yaxis_title='Average Sales',font=dict(size=20,family='bold'))

fig.show()

In [104]:
data=go.Scatter(x=groupby_year_df['Prices-Category'][0:3],y=groupby_year_df['sales_small.SalesVolume'][0:3],mode='lines+markers',marker_color='navy', name='2015')
layout=go.Layout(title='Price category vs avg sales in both years' ,xaxis_title='Price Category',yaxis_title='Average Sales')
fig = go.Figure(data=data, layout=layout)
fig.add_trace(go.Scatter(x=groupby_year_df['Prices-Category'][0:3], y=groupby_year_df['sales_small.SalesVolume'][3:], mode='lines+markers', name='2016',marker_color='skyblue'))
pyo.iplot(fig);

In [105]:
index_names = merged_df[ merged_df['Prices-Category'] == 'Other' ].index
merged_df.drop(index_names, inplace = True)

#groupby_year_df=merged_df.groupby(['Prices-Category','Year'],sort=False)['sales_small.SalesVolume'].mean()
#groupby_year_df=groupby_year_df.reset_index()

In [106]:
merged_df_2015_osp=merged_df[merged_df['Prices-Category']=='OSP']
groupby_month_osp=merged_df_2015_osp.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_osp=groupby_month_osp.reset_index()
groupby_month_osp['Year-Month']=pd.to_datetime(groupby_month_osp['Year-Month'],format='%B-%Y')
groupby_month_osp=groupby_month_osp.sort_values(by=['Year-Month']) 
groupby_month_osp

Year-Month  sales_small.SalesVolume
0  2015-01-01                13.069382
1  2015-02-01                20.182177
2  2015-03-01                18.813503
3  2015-04-01                18.491547
4  2015-05-01                15.814748
6  2015-06-01                11.038978
7  2015-07-01                 2.021978
8  2015-08-01                 1.367347
9  2015-09-01                 7.709091
10 2015-10-01                22.124812
5  2015-11-01                18.382097
11 2015-12-01                15.878269
12 2016-01-01                13.786102
13 2016-02-01                10.406699

In [107]:
merged_df_2015_prev=merged_df[merged_df['Prices-Category']=='Previous CSP']
groupby_month_prev=merged_df_2015_prev.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_prev=groupby_month_prev.reset_index()
groupby_month_prev['Year-Month']=pd.to_datetime(groupby_month_prev['Year-Month'],format='%B-%Y')
groupby_month_prev=groupby_month_prev.sort_values(by=['Year-Month']) 
groupby_month_prev

Year-Month  sales_small.SalesVolume
13 2015-01-01                 4.794118
0  2015-02-01                42.237288
1  2015-03-01                23.457627
2  2015-04-01                28.076063
3  2015-05-01                21.785150
4  2015-06-01                11.476065
5  2015-07-01                 4.679313
6  2015-08-01                 2.633028
7  2015-09-01                 0.944368
8  2015-10-01                 1.190916
9  2015-11-01                 2.198839
10 2015-12-01                 6.069420
11 2016-01-01                 5.268587
12 2016-02-01                 7.452650

In [108]:
merged_df_2015_csp=merged_df[merged_df['Prices-Category']=='CSP']
groupby_month_csp=merged_df_2015_csp.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_csp=groupby_month_csp.reset_index()
groupby_month_csp['Year-Month']=pd.to_datetime(groupby_month_csp['Year-Month'],format='%B-%Y')
groupby_month_csp=groupby_month_csp.sort_values(by=['Year-Month']) 
groupby_month_csp

Year-Month  sales_small.SalesVolume
13 2015-01-01                 5.652174
0  2015-02-01                43.878788
1  2015-03-01                23.342723
2  2015-04-01                26.086785
3  2015-05-01                19.370625
4  2015-06-01                10.261115
5  2015-07-01                 4.372690
6  2015-08-01                 2.401589
7  2015-09-01                 0.924908
8  2015-10-01                 0.719885
9  2015-11-01                 1.533561
10 2015-12-01                 5.038513
11 2016-01-01                 4.057221
12 2016-02-01                 6.657208

In [109]:
data=go.Scatter(x=groupby_month_osp['Year-Month'],y=groupby_month_osp['sales_small.SalesVolume'],mode='lines+markers',marker_color='navy', name='OSP')
layout=go.Layout(title='Average Sales of the 3 Prices 2015 ' ,xaxis_title='Month',yaxis_title='Sales Volume',xaxis=dict(dtick='M1'))
fig = go.Figure(data=data, layout=layout)
fig.add_trace(go.Scatter(x=groupby_month_prev['Year-Month'], y=groupby_month_prev['sales_small.SalesVolume'], mode='lines+markers', name='Previous CSP',marker_color='#0097A9'))
fig.add_trace(go.Scatter(x=groupby_month_csp['Year-Month'], y=groupby_month_csp['sales_small.SalesVolume'], mode='lines+markers', name='CSP',marker_color='lightsalmon'))
pyo.iplot(fig);

In [110]:
summer_df=pd.DataFrame()
summer_df=summer_df.append(merged_df[merged_df['Year-Month']=='June-2015'])
summer_df=summer_df.append(merged_df[merged_df['Year-Month']=='July-2015'])
summer_df=summer_df.append(merged_df[merged_df['Year-Month']=='August-2015'])
summer_df=summer_df.append(merged_df[merged_df['Year-Month']=='September-2015'])
summer_df.head()

ProductID Channel_x  ... price_changes.CSP  Prices-Category
86  135fc45e    Stores  ...            13.133              CSP
87  135fc45e    Stores  ...            10.882     Previous CSP
90  135fc45e    Stores  ...            13.133              CSP
91  135fc45e    Stores  ...            10.882     Previous CSP
94  135fc45e    Stores  ...            13.133              CSP

[5 rows x 24 columns]

In [111]:
merged_df_2015_osp=merged_df[(merged_df['Year']==2016) & (merged_df['Prices-Category']=='OSP')]
groupby_month_osp=merged_df_2015_osp.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_osp=groupby_month_osp.reset_index()
groupby_month_osp['Year-Month']=pd.to_datetime(groupby_month_osp['Year-Month'],format='%B-%Y')
groupby_month_osp=groupby_month_osp.sort_values(by=['Year-Month']) 
merged_df_2015_csp=merged_df[(merged_df['Year']==2016) & (merged_df['Prices-Category']=='CSP')]
groupby_month_csp=merged_df_2015_csp.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_csp=groupby_month_csp.reset_index()
groupby_month_csp['Year-Month']=pd.to_datetime(groupby_month_csp['Year-Month'],format='%B-%Y')
groupby_month_csp=groupby_month_csp.sort_values(by=['Year-Month']) 
merged_df_2015_prev=merged_df[(merged_df['Year']==2016) & (merged_df['Prices-Category']=='Previous CSP')]
groupby_month_prev=merged_df_2015_prev.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()
groupby_month_prev=groupby_month_prev.reset_index()
groupby_month_prev['Year-Month']=pd.to_datetime(groupby_month_prev['Year-Month'],format='%B-%Y')
groupby_month_prev=groupby_month_prev.sort_values(by=['Year-Month']) 
data=go.Scatter(x=groupby_month_osp['Year-Month'],y=groupby_month_osp['sales_small.SalesVolume'].values,mode='lines+markers',marker_color='navy', name='OSP')
layout=go.Layout(title='Average Sales of the 3 Prices 2016 ' ,xaxis_title='Month',yaxis_title='Sales Volume',xaxis=dict(dtick='M1'))
fig = go.Figure(data=data, layout=layout)
fig.add_trace(go.Scatter(x=groupby_month_prev['Year-Month'], y=groupby_month_prev['sales_small.SalesVolume'], mode='lines+markers', name='Previous CSP',marker_color='#0097A9'))
fig.add_trace(go.Scatter(x=groupby_month_csp['Year-Month'], y=groupby_month_csp['sales_small.SalesVolume'], mode='lines+markers', name='Previous CSP',marker_color='lightsalmon'))
pyo.iplot(fig);


In [112]:
#groupby(['Prices-Category'],sort=False)['sales_small.SalesVolume'].mean()
summer_df_price_cat=summer_df['Prices-Category'].value_counts()
summer_df_price_cat=summer_df_price_cat.reset_index()
fig = go.Figure(data=go.Pie(labels=summer_df_price_cat['index'],values=summer_df_price_cat['Prices-Category']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=18,
                  marker=dict(colors=['skyblue','navy','grey'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of products of each Price Category in summer')
fig.show()
summer_df_price_cat

index  Prices-Category
0           CSP            20603
1  Previous CSP            12347
2           OSP              939

In [113]:
winter_df=pd.DataFrame()
winter_df=winter_df.append(merged_df[merged_df['Year-Month']=='January-2015'])
winter_df=winter_df.append(merged_df[merged_df['Year-Month']=='February-2015'])
winter_df=winter_df.append(merged_df[merged_df['Year-Month']=='March-2015'])
winter_df=winter_df.append(merged_df[merged_df['Year-Month']=='April-2015'])
winter_df=winter_df.append(merged_df[merged_df['Year-Month']=='May-2015'])
winter_df.head()

ProductID Channel_x  ... price_changes.CSP  Prices-Category
0  135fc45e    Stores  ...            16.283              OSP
1  135fc45e    Stores  ...            14.483              OSP
2  135fc45e    Stores  ...            13.133              OSP
3  135fc45e    Stores  ...            10.882              OSP
4  135fc45e    Stores  ...            16.283              OSP

[5 rows x 24 columns]

In [114]:
winter_df_price_cat=winter_df['Prices-Category'].value_counts()
winter_df_price_cat=winter_df_price_cat.reset_index()
fig = go.Figure(data=go.Pie(labels=winter_df_price_cat['index'],values=winter_df_price_cat['Prices-Category']))
fig.update_traces(hoverinfo='label+percent', textinfo='label+percent', textfont_size=20,
                  marker=dict(colors=['grey','skyblue','navy'], line=dict(color='#000000', width=2)))
fig.update_layout(title='Percentage of products of each Price Category before summer')
fig.show()

In [117]:
index_names = summer_df[ summer_df['Prices-Category'] == 'Other' ].index
summer_df.drop(index_names, inplace = True)
index_names = winter_df[ winter_df['Prices-Category'] == 'Other' ].index
winter_df.drop(index_names, inplace = True)

In [118]:

summer_groupby=summer_df.groupby(['Prices-Category'],sort=False)['sales_small.SalesVolume'].mean()
summer_groupby=summer_groupby.reset_index()
summer_groupby

Prices-Category  sales_small.SalesVolume
0             CSP                 4.623501
1    Previous CSP                 5.591480
2             OSP                 9.465389

In [119]:
winter_groupby=winter_df.groupby(['Prices-Category'],sort=False)['sales_small.SalesVolume'].mean()
winter_groupby=winter_groupby.reset_index()
winter_groupby

Prices-Category  sales_small.SalesVolume
0             OSP                18.085938
1             CSP                21.010998
2    Previous CSP                23.428772

In [120]:
fig = go.Figure(data=[
    go.Bar(name='Summer', x=summer_groupby['Prices-Category'], y=summer_groupby['sales_small.SalesVolume'],marker_color='skyblue'),
    go.Bar(name='Before Summer', x=winter_groupby['Prices-Category'], y=winter_groupby['sales_small.SalesVolume'],marker_color='navy')

])
# Change the bar mode
fig.update_layout(barmode='group',title='Price Categories average sales in summer and before',
                  xaxis_title='Price Category',yaxis_title='Average Sales',font=dict(size=20,family='bold'))

fig.show()

In [121]:
data=go.Scatter(x=merged_df['sales_small.CSP'],y=merged_df['sales_small.SalesVolume'],mode='markers',marker_color='blue')
layout=go.Layout(title='Relation between price and sales volume' ,xaxis_title='price',yaxis_title='Sales Volume')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);

In [122]:
merged_df2=merged_df[merged_df['Year']==2015]
merged_df2.head()

ProductID Channel_x  ... price_changes.CSP  Prices-Category
0  135fc45e    Stores  ...            16.283              OSP
1  135fc45e    Stores  ...            14.483              OSP
2  135fc45e    Stores  ...            13.133              OSP
3  135fc45e    Stores  ...            10.882              OSP
4  135fc45e    Stores  ...            16.283              OSP

[5 rows x 24 columns]

In [123]:
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.pipeline import make_pipeline
model_df=merged_df2.copy()
x=model_df['sales_small.CSP'].values.reshape(-1,1)
y=model_df['sales_small.SalesVolume']
poly_f=PolynomialFeatures(3)
x_poly=poly_f.fit_transform(x)
lin_reg=LinearRegression()
lin_reg.fit(x_poly,y)
model_df['model'] = lin_reg.predict(x_poly)
# figure setup and trace for observations
fig = go.Figure()
#fig.add_trace(go.Scatter(x=model_df['sales_small.CSP'], y=model_df['sales_small.SalesVolume'], mode='markers', name='observations'))

# trace for polynomial model
#model_df = model_df.sort_values(by=['model'])
#print(type(df['total_bill'].values))
fig.add_trace(go.Scatter(x=model_df['sales_small.CSP'], y=model_df['model'], mode='markers', name='model'))
fig.update_layout(yaxis=dict(range=[0, 20]))
fig.show()

In [124]:
model_df.head()

ProductID Channel_x Country_x  ...  price_changes.CSP  Prices-Category      model
0  135fc45e    Stores         B  ...             16.283              OSP  11.399963
1  135fc45e    Stores         B  ...             14.483              OSP  11.399963
2  135fc45e    Stores         B  ...             13.133              OSP  11.399963
3  135fc45e    Stores         B  ...             10.882              OSP  11.399963
4  135fc45e    Stores         B  ...             16.283              OSP  11.399963

[5 rows x 25 columns]

In [125]:
df_weekly_sales17=model_df.groupby(['Year-Month'],sort=False)['sales_small.SalesVolume'].mean()

In [126]:
trace = go.Bar(x=list(df_weekly_sales17.index), y=list(df_weekly_sales17.values), marker=dict(color='navy'))
data=[trace]
layout = go.Layout(title='Predicted 2017 average sales for every Month based on historical prices and sales',xaxis=dict(type='category',tickangle=45),xaxis_title='Month',yaxis_title='Predicted Average Sales Volume')
fig = go.Figure(data=data, layout=layout)
fig.update_layout(yaxis=dict(range=[0, 20]))
pyo.iplot(fig);

In [127]:
data=go.Scatter(x=df_weekly_sales17.index,y=df_weekly_sales17.values,mode='lines+markers',marker_color='navy', name='Predicted Sales 2017')
layout=go.Layout(title='Actual Sales 2015 vs Predicted sales 2017' ,xaxis_title='Month',yaxis_title='Sales Volume')
fig = go.Figure(data=data, layout=layout)
fig.add_trace(go.Scatter(x=df_weekly_sales15.index, y=df_weekly_sales15.values, mode='lines+markers', name='Actual Sales 2015',marker_color='#0097A9'))
pyo.iplot(fig);

In [128]:
merged_df3=merged_df2[merged_df2['Prices-Category']=='OSP']
merged_df3[ merged_df3['Year-Month']=='July-2015']

ProductID Channel_x  ... price_changes.CSP  Prices-Category
30018   fd33a12b    Stores  ...            12.232              OSP
30019   fd33a12b    Stores  ...            12.232              OSP
30020   fd33a12b    Stores  ...            12.232              OSP
30021   fd33a12b    Stores  ...            12.232              OSP
69165   f4d8c2f8    Online  ...            12.683              OSP
...          ...       ...  ...               ...              ...
222481  eae69e99    Online  ...            10.882              OSP
222482  eae69e99    Online  ...            10.882              OSP
222483  eae69e99    Online  ...            10.882              OSP
222514  46b3a979    Online  ...            10.882              OSP
222515  46b3a979    Online  ...            10.882              OSP

[91 rows x 24 columns]

In [131]:
prices_cat_counts=merged_df['Prices-Category'].value_counts()
prices_cat_counts

CSP             50733
OSP             39027
Previous CSP    25908
Name: Prices-Category, dtype: int64

In [132]:
trace = go.Bar(x=prices_cat_counts.index, y=prices_cat_counts.values, marker=dict(color='skyblue'))
data=[trace]
layout = go.Layout(title='number of products for each price category ',xaxis=dict(type='category',categoryorder='total descending'),xaxis_title='Price Category',yaxis_title='Nu,')
fig = go.Figure(data=data, layout=layout)
pyo.iplot(fig);